In [1]:
! pip install shap

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 540.1/540.1 kB 3.4 MB/s eta 0:00:000m eta -:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 15.1 MB/s eta 0:00:0031m17.3 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.9/43.9 MB 27.9 MB/s eta 0:00:00m eta 0:00:010:00:01


## Bert + Shap

In [19]:
from transformers import AutoModel
model_path = '../src/models/weights/bert'
# model = AutoModel.from_pretrained(model_path)

import sys 
sys.path.append('../src')
import torch
from models.transformer_based_models import load_and_prepare_model, train_and_evaluate

num_labels = 2  # Ensure this matches the original setup
model = load_and_prepare_model('bert', num_labels=num_labels)
model.load_state_dict(torch.load('../src/models/weights/bert_model.pth'))
# model.eval()

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/tmp/ipykernel_888973/3530050531.py:12: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We

<All keys matched successfully>

In [10]:
model

PeftModel(
  (base_model): LoraModel(
    (model): BertForSequenceClassification(
      (bert): BertModel(
        (embeddings): BertEmbeddings(
          (word_embeddings): Embedding(30522, 768, padding_idx=0)
          (position_embeddings): Embedding(512, 768)
          (token_type_embeddings): Embedding(2, 768)
          (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (encoder): BertEncoder(
          (layer): ModuleList(
            (0-11): 12 x BertLayer(
              (attention): BertAttention(
                (self): BertSdpaSelfAttention(
                  (query): lora.Linear(
                    (base_layer): Linear(in_features=768, out_features=768, bias=True)
                    (lora_dropout): ModuleDict(
                      (default): Dropout(p=0.01, inplace=False)
                    )
                    (lora_A): ModuleDict(
                      (default): Linear(in_features=76

In [20]:
import pandas as pd
import json
with open('../data/processed/test_split_processed.json') as f:
  data = json.load(f)
d = pd.DataFrame.from_dict(data)
d



input  \
0      \nCompose a comprehensive description of the i...   
1      Explain the visual content of the image in gre...   
2      \nCompose a comprehensive description of the i...   
3      Write a detailed description of the given imag...   
4      \nDelve into the details of the image and comp...   
...                                                  ...   
10063  Delve into the details of the image and compos...   
10064  \nCompose a comprehensive description of the i...   
10065  \nCan you elaborate on the elements of the pic...   
10066  Compose a detailed account of the image, encom...   
10067  \nCompose a detailed account of the image, enc...   

                                                response  \
0      The image features a cake that has been cut in...   
1      The image features a tray with a hot dog and a...   
2      The image features a city street with a bus dr...   
3      The image depicts a beautiful beach scene with...   
4      The image features a fire hydrant painted in r...   
...                                                  ...   
10063  In the image, a young man is feeding a giraffe...   
10064  The image depicts a colorful parade on a city ...   
10065  The image features a large red semi-truck park...   
10066  In the image, two people are riding in a small...   
10067  In the image, there is a large body of water, ...   

                                           full_sentence  label  
0      The scene is set in a dimly lit room, which ad...      0  
1      The hot dog is placed in the middle of the tra...      0  
2      The scene is characterized by the hustle and b...      0  
3      The image depicts a beautiful beach scene with...      0  
4      Additionally, there is a yellow curb surroundi...      0  
...                                                  ...    ...  
10063  The man is wearing a black sweatshirt, and the...      0  
10064  The truck is carrying a group of people, who a...      0  
10065  Some of these vehicles are parked close to the...      1  
10066  The water is lush and green, providing a seren...      0  
10067  In the image, there is a large body of water, ...      1  

[10068 rows x 4 columns]

In [21]:
sample = pd.concat([d.loc[d['label']==1].sample(5), d.loc[d['label']==0].sample(5)], axis = 0)
sample

input  \
4071  \nExplain the visual content of the image in g...   
6108                    \nDescribe the following image.   
9986  \nCompose a detailed account of the image, enc...   
4304  Compose a comprehensive description of the ima...   
8560  Please provide a detailed description of the i...   
5638  Delve into the details of the image and compos...   
8554  Please provide a detailed description of the i...   
5848                       What is this photo about'?\n   
3256  Provide an intricate description of the image,...   
695   Please provide a detailed description of the i...   

                                               response  \
4071  The image features a group of three zebras sta...   
6108  The image features a person wearing a motorcyc...   
9986  In the image, there is a pizza on a white plat...   
4304  The image is a close-up of a pizza on a table,...   
8560  The image features a blue mug filled with a wh...   
5638  In the image, a young boy is standing in front...   
8554  The image features a close-up of a bunch of ri...   
5848  The image features two white plates placed on ...   
3256  In the image, a farmer's market is showcasing ...   
695   In the image, there is a large bunch of banana...   

                                          full_sentence  label  
4071  In the background, there is a wooden fence tha...      1  
6108  There are several cars scattered throughout th...      1  
9986  A knife, fork, and spoon are also present on t...      1  
4304  The image is a close-up of a pizza on a table,...      1  
8560  The cat figurine is placed inside the mug, whi...      1  
5638  In the image, a young boy is standing in front...      0  
8554  Overall, the image showcases a colorful and ap...      0  
5848  The plates are positioned close to each other,...      0  
3256  Overall, the image captures the vibrant colors...      0  
695   In the image, there is a large bunch of banana...      0

In [22]:
import transformers
from transformers import AutoTokenizer
import shap
pred = transformers.pipeline(
    "text-classification",
    model=model.base_model.model,
    tokenizer=AutoTokenizer.from_pretrained(model_path),
    device=0,
    return_all_scores=True,
)


/home/maiya.goloburda/miniconda3/envs/vlm-hallucinations/lib/python3.10/site-packages/transformers/pipelines/text_classification.py:106: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


In [23]:
explainer = shap.Explainer(pred)


shap_values = explainer(sample["full_sentence"])


PartitionExplainer explainer: 11it [00:40,  5.05s/it]                        


In [24]:
from IPython.core.display import display, HTML
# Create the SHAP text plot
shap.plots.text(shap_values)

# # Save the plot as a PNG file
# plt.savefig("shap_text_plot.png", dpi=300, bbox_inches="tight")

/tmp/ipykernel_888973/3410706138.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython.display
  from IPython.core.display import display, HTML


In [24]:
! python3 -m pip install matplotlib